<a href="https://colab.research.google.com/github/maryam-w07/StyleTTS2/blob/main/StyleTTS2_demo.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

### Install packages and download models

In [ ]:
!pip install torch==2.5.0 torchvision torchaudio --index-url https://download.pytorch.org/whl/cu121


Looking in indexes: https://download.pytorch.org/whl/cu121
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 780.5/780.5 MB 571.9 kB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 23.7/23.7 MB 21.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 823.6/823.6 kB 23.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.1/14.1 MB 28.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 410.6/410.6 MB 1.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 121.6/121.6 MB 7.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.5/56.5 MB 12.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 124.2/124.2 MB 8.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 196.0/196.0 MB 1.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 99.1/99.1 kB 6.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 209.5/209.5 MB 5.4 MB/s eta 0:00:00
INFO: pip is looking at multiple versions of torchv

In [17]:
!rm -rf /content/StyleTTS2


In [1]:
%%shell
git clone https://github.com/maryam-w07/StyleTTS2.git
cd StyleTTS2
pip install SoundFile torchaudio munch torch pydub pyyaml librosa nltk matplotlib accelerate transformers phonemizer einops einops-exts tqdm typing-extensions git+https://github.com/resemble-ai/monotonic_align.git
sudo apt-get install espeak-ng
git-lfs clone https://huggingface.co/yl4579/StyleTTS2-LibriTTS
mv StyleTTS2-LibriTTS/Models .
mv StyleTTS2-LibriTTS/reference_audio.zip .
unzip reference_audio.zip
mv reference_audio Demo/reference_audio


Cloning into 'StyleTTS2'...
remote: Enumerating objects: 390, done.
remote: Counting objects: 100% (162/162), done.
remote: Compressing objects: 100% (66/66), done.
remote: Total 390 (delta 114), reused 96 (delta 96), pack-reused 228 (from 1)
Receiving objects: 100% (390/390), 133.98 MiB | 12.94 MiB/s, done.
Resolving deltas: 100% (215/215), done.
Updating files: 100% (49/49), done.
  Cloning https://github.com/resemble-ai/monotonic_align.git to /tmp/pip-req-build-ws1gjy0d
  Running command git clone --filter=blob:none --quiet https://github.com/resemble-ai/monotonic_align.git /tmp/pip-req-build-ws1gjy0d
  Resolved https://github.com/resemble-ai/monotonic_align.git to commit c6e5e6cb19882164027eb6e35118e841eed9298e
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.2/48.2 kB 4.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4

In [ ]:
from huggingface_hub import notebook_login

notebook_login()

### Load models

In [2]:
import nltk
nltk.download('punkt')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

In [3]:
import torch
torch.manual_seed(0)
torch.backends.cudnn.benchmark = False
torch.backends.cudnn.deterministic = True

import random
random.seed(0)

import numpy as np
np.random.seed(0)

# load packages
import time
import random
import yaml
from munch import Munch
import numpy as np
import torch
from torch import nn
import torch.nn.functional as F
import torchaudio
import librosa
from nltk.tokenize import word_tokenize

#from models import *
#from utils import *
#from text_utils import TextCleaner
#textclenaer = TextCleaner()

In [ ]:
%cd StyleTTS2

import torch
torch.manual_seed(0)
torch.backends.cudnn.benchmark = False
torch.backends.cudnn.deterministic = True

import random
random.seed(0)

import numpy as np
np.random.seed(0)

# load packages
import time
import random
import yaml
from munch import Munch
import numpy as np
import torch
from torch import nn
import torch.nn.functional as F
import torchaudio
import librosa
from nltk.tokenize import word_tokenize

from models import *
from utils import *
from text_utils import TextCleaner
textclenaer = TextCleaner()

%matplotlib inline

to_mel = torchaudio.transforms.MelSpectrogram(
    n_mels=80, n_fft=2048, win_length=1200, hop_length=300)
mean, std = -4, 4

def length_to_mask(lengths):
    mask = torch.arange(lengths.max()).unsqueeze(0).expand(lengths.shape[0], -1).type_as(lengths)
    mask = torch.gt(mask+1, lengths.unsqueeze(1))
    return mask

def preprocess(wave):
    wave_tensor = torch.from_numpy(wave).float()
    mel_tensor = to_mel(wave_tensor)
    mel_tensor = (torch.log(1e-5 + mel_tensor.unsqueeze(0)) - mean) / std
    return mel_tensor

def compute_style(path):
    wave, sr = librosa.load(path, sr=24000)
    audio, index = librosa.effects.trim(wave, top_db=30)
    if sr != 24000:
        audio = librosa.resample(audio, sr, 24000)
    mel_tensor = preprocess(audio).to(device)

    with torch.no_grad():
        ref_s = model.style_encoder(mel_tensor.unsqueeze(1))
        ref_p = model.predictor_encoder(mel_tensor.unsqueeze(1))

    return torch.cat([ref_s, ref_p], dim=1)

device = 'cuda' if torch.cuda.is_available() else 'cpu'

# load phonemizer
import phonemizer
global_phonemizer = phonemizer.backend.EspeakBackend(language='en-us', preserve_punctuation=True,  with_stress=True)

config = yaml.safe_load(open("Models/LibriTTS/config.yml"))

# load pretrained ASR model
ASR_config = config.get('ASR_config', False)
ASR_path = config.get('ASR_path', False)
text_aligner = load_ASR_models(ASR_path, ASR_config)

# load pretrained F0 model
F0_path = config.get('F0_path', False)
pitch_extractor = load_F0_models(F0_path)

# load BERT model
from Utils.PLBERT.util import load_plbert
BERT_path = config.get('PLBERT_dir', False)
plbert = load_plbert(BERT_path)

model_params = recursive_munch(config['model_params'])
model = build_model(model_params, text_aligner, pitch_extractor, plbert)
_ = [model[key].eval() for key in model]
_ = [model[key].to(device) for key in model]

params_whole = torch.load("Models/LibriTTS/epochs_2nd_00020.pth", map_location='cpu')
params = params_whole['net']

for key in model:
    if key in params:
        print('%s loaded' % key)
        try:
            model[key].load_state_dict(params[key])
        except:
            from collections import OrderedDict
            state_dict = params[key]
            new_state_dict = OrderedDict()
            for k, v in state_dict.items():
                name = k[7:] # remove `module.`
                new_state_dict[name] = v
            # load params
            model[key].load_state_dict(new_state_dict, strict=False)
#             except:
#                 _load(params[key], model[key])
_ = [model[key].eval() for key in model]

from Modules.diffusion.sampler import DiffusionSampler, ADPM2Sampler, KarrasSchedule

sampler = DiffusionSampler(
    model.diffusion.diffusion,
    sampler=ADPM2Sampler(),
    sigma_schedule=KarrasSchedule(sigma_min=0.0001, sigma_max=3.0, rho=9.0), # empirical parameters
    clamp=False
)

def inference(text, ref_s, alpha = 0.3, beta = 0.7, diffusion_steps=5, embedding_scale=1):
    text = text.strip()
    ps = global_phonemizer.phonemize([text])
    #ps = word_tokenize(ps[0])
    ps = ps[0].split() #for errkr
    ps = ' '.join(ps)
    tokens = textclenaer(ps)
    tokens.insert(0, 0)
    tokens = torch.LongTensor(tokens).to(device).unsqueeze(0)

    with torch.no_grad():
        input_lengths = torch.LongTensor([tokens.shape[-1]]).to(device)
        text_mask = length_to_mask(input_lengths).to(device)

        t_en = model.text_encoder(tokens, input_lengths, text_mask)
        bert_dur = model.bert(tokens, attention_mask=(~text_mask).int())
        d_en = model.bert_encoder(bert_dur).transpose(-1, -2)

        s_pred = sampler(noise = torch.randn((1, 256)).unsqueeze(1).to(device),
                                          embedding=bert_dur,
                                          embedding_scale=embedding_scale,
                                            features=ref_s, # reference from the same speaker as the embedding
                                             num_steps=diffusion_steps).squeeze(1)


        s = s_pred[:, 128:]
        ref = s_pred[:, :128]

        ref = alpha * ref + (1 - alpha)  * ref_s[:, :128]
        s = beta * s + (1 - beta)  * ref_s[:, 128:]

        d = model.predictor.text_encoder(d_en,
                                         s, input_lengths, text_mask)

        x, _ = model.predictor.lstm(d)
        duration = model.predictor.duration_proj(x)

        duration = torch.sigmoid(duration).sum(axis=-1)
        pred_dur = torch.round(duration.squeeze()).clamp(min=1)


        pred_aln_trg = torch.zeros(input_lengths, int(pred_dur.sum().data))
        c_frame = 0
        for i in range(pred_aln_trg.size(0)):
            pred_aln_trg[i, c_frame:c_frame + int(pred_dur[i].data)] = 1
            c_frame += int(pred_dur[i].data)

        # encode prosody
        en = (d.transpose(-1, -2) @ pred_aln_trg.unsqueeze(0).to(device))
        if model_params.decoder.type == "hifigan":
            asr_new = torch.zeros_like(en)
            asr_new[:, :, 0] = en[:, :, 0]
            asr_new[:, :, 1:] = en[:, :, 0:-1]
            en = asr_new

        F0_pred, N_pred = model.predictor.F0Ntrain(en, s)

        asr = (t_en @ pred_aln_trg.unsqueeze(0).to(device))
        if model_params.decoder.type == "hifigan":
            asr_new = torch.zeros_like(asr)
            asr_new[:, :, 0] = asr[:, :, 0]
            asr_new[:, :, 1:] = asr[:, :, 0:-1]
            asr = asr_new

        out = model.decoder(asr,
                                F0_pred, N_pred, ref.squeeze().unsqueeze(0))


    return out.squeeze().cpu().numpy()[..., :-50] # weird pulse at the end of the model, need to be fixed later

def LFinference(text, s_prev, ref_s, alpha = 0.3, beta = 0.7, t = 0.7, diffusion_steps=5, embedding_scale=1):
  text = text.strip()
  ps = global_phonemizer.phonemize([text])
  ps = word_tokenize(ps[0])
  ps = ' '.join(ps)
  ps = ps.replace('``', '"')
  ps = ps.replace("''", '"')

  tokens = textclenaer(ps)
  tokens.insert(0, 0)
  tokens = torch.LongTensor(tokens).to(device).unsqueeze(0)

  with torch.no_grad():
      input_lengths = torch.LongTensor([tokens.shape[-1]]).to(device)
      text_mask = length_to_mask(input_lengths).to(device)

      t_en = model.text_encoder(tokens, input_lengths, text_mask)
      bert_dur = model.bert(tokens, attention_mask=(~text_mask).int())
      d_en = model.bert_encoder(bert_dur).transpose(-1, -2)

      s_pred = sampler(noise = torch.randn((1, 256)).unsqueeze(1).to(device),
                                        embedding=bert_dur,
                                        embedding_scale=embedding_scale,
                                          features=ref_s, # reference from the same speaker as the embedding
                                            num_steps=diffusion_steps).squeeze(1)

      if s_prev is not None:
          # convex combination of previous and current style
          s_pred = t * s_prev + (1 - t) * s_pred

      s = s_pred[:, 128:]
      ref = s_pred[:, :128]

      ref = alpha * ref + (1 - alpha)  * ref_s[:, :128]
      s = beta * s + (1 - beta)  * ref_s[:, 128:]

      s_pred = torch.cat([ref, s], dim=-1)

      d = model.predictor.text_encoder(d_en,
                                        s, input_lengths, text_mask)

      x, _ = model.predictor.lstm(d)
      duration = model.predictor.duration_proj(x)

      duration = torch.sigmoid(duration).sum(axis=-1)
      pred_dur = torch.round(duration.squeeze()).clamp(min=1)


      pred_aln_trg = torch.zeros(input_lengths, int(pred_dur.sum().data))
      c_frame = 0
      for i in range(pred_aln_trg.size(0)):
          pred_aln_trg[i, c_frame:c_frame + int(pred_dur[i].data)] = 1
          c_frame += int(pred_dur[i].data)

      # encode prosody
      en = (d.transpose(-1, -2) @ pred_aln_trg.unsqueeze(0).to(device))
      if model_params.decoder.type == "hifigan":
          asr_new = torch.zeros_like(en)
          asr_new[:, :, 0] = en[:, :, 0]
          asr_new[:, :, 1:] = en[:, :, 0:-1]
          en = asr_new

      F0_pred, N_pred = model.predictor.F0Ntrain(en, s)

      asr = (t_en @ pred_aln_trg.unsqueeze(0).to(device))
      if model_params.decoder.type == "hifigan":
          asr_new = torch.zeros_like(asr)
          asr_new[:, :, 0] = asr[:, :, 0]
          asr_new[:, :, 1:] = asr[:, :, 0:-1]
          asr = asr_new

      out = model.decoder(asr,
                              F0_pred, N_pred, ref.squeeze().unsqueeze(0))


  return out.squeeze().cpu().numpy()[..., :-100], s_pred # weird pulse at the end of the model, need to be fixed later

def STinference(text, ref_s, ref_text, alpha = 0.3, beta = 0.7, diffusion_steps=5, embedding_scale=1):
    text = text.strip()
    ps = global_phonemizer.phonemize([text])
    ps = word_tokenize(ps[0])
    ps = ' '.join(ps)

    tokens = textclenaer(ps)
    tokens.insert(0, 0)
    tokens = torch.LongTensor(tokens).to(device).unsqueeze(0)

    ref_text = ref_text.strip()
    ps = global_phonemizer.phonemize([ref_text])
    ps = word_tokenize(ps[0])
    ps = ' '.join(ps)

    ref_tokens = textclenaer(ps)
    ref_tokens.insert(0, 0)
    ref_tokens = torch.LongTensor(ref_tokens).to(device).unsqueeze(0)


    with torch.no_grad():
        input_lengths = torch.LongTensor([tokens.shape[-1]]).to(device)
        text_mask = length_to_mask(input_lengths).to(device)

        t_en = model.text_encoder(tokens, input_lengths, text_mask)
        bert_dur = model.bert(tokens, attention_mask=(~text_mask).int())
        d_en = model.bert_encoder(bert_dur).transpose(-1, -2)

        ref_input_lengths = torch.LongTensor([ref_tokens.shape[-1]]).to(device)
        ref_text_mask = length_to_mask(ref_input_lengths).to(device)
        ref_bert_dur = model.bert(ref_tokens, attention_mask=(~ref_text_mask).int())
        s_pred = sampler(noise = torch.randn((1, 256)).unsqueeze(1).to(device),
                                          embedding=bert_dur,
                                          embedding_scale=embedding_scale,
                                            features=ref_s, # reference from the same speaker as the embedding
                                             num_steps=diffusion_steps).squeeze(1)


        s = s_pred[:, 128:]
        ref = s_pred[:, :128]

        ref = alpha * ref + (1 - alpha)  * ref_s[:, :128]
        s = beta * s + (1 - beta)  * ref_s[:, 128:]

        d = model.predictor.text_encoder(d_en,
                                         s, input_lengths, text_mask)

        x, _ = model.predictor.lstm(d)
        duration = model.predictor.duration_proj(x)

        duration = torch.sigmoid(duration).sum(axis=-1)
        pred_dur = torch.round(duration.squeeze()).clamp(min=1)


        pred_aln_trg = torch.zeros(input_lengths, int(pred_dur.sum().data))
        c_frame = 0
        for i in range(pred_aln_trg.size(0)):
            pred_aln_trg[i, c_frame:c_frame + int(pred_dur[i].data)] = 1
            c_frame += int(pred_dur[i].data)

        # encode prosody
        en = (d.transpose(-1, -2) @ pred_aln_trg.unsqueeze(0).to(device))
        if model_params.decoder.type == "hifigan":
            asr_new = torch.zeros_like(en)
            asr_new[:, :, 0] = en[:, :, 0]
            asr_new[:, :, 1:] = en[:, :, 0:-1]
            en = asr_new

        F0_pred, N_pred = model.predictor.F0Ntrain(en, s)

        asr = (t_en @ pred_aln_trg.unsqueeze(0).to(device))
        if model_params.decoder.type == "hifigan":
            asr_new = torch.zeros_like(asr)
            asr_new[:, :, 0] = asr[:, :, 0]
            asr_new[:, :, 1:] = asr[:, :, 0:-1]
            asr = asr_new

        out = model.decoder(asr,
                                F0_pred, N_pred, ref.squeeze().unsqueeze(0))


    return out.squeeze().cpu().numpy()[..., :-50] # weird pulse at the end of the model, need to be fixed later


[Errno 2] No such file or directory: 'StyleTTS2'
/content/StyleTTS2
177


UnpicklingError: Weights only load failed. This file can still be loaded, to do so you have two options, [1mdo those steps only if you trust the source of the checkpoint[0m. 
	(1) In PyTorch 2.6, we changed the default value of the `weights_only` argument in `torch.load` from `False` to `True`. Re-running `torch.load` with `weights_only` set to `False` will likely succeed, but it can result in arbitrary code execution. Do it only if you got the file from a trusted source.
	(2) Alternatively, to load with `weights_only=True` please check the recommended steps in the following error message.
	WeightsUnpickler error: Unsupported global: GLOBAL builtins.getattr was not an allowed global by default. Please use `torch.serialization.add_safe_globals([getattr])` or the `torch.serialization.safe_globals([getattr])` context manager to allowlist this global if you trust this class/function.

Check the documentation of torch.load to learn more about types accepted by default with weights_only ht

In [ ]:
!grep -r "load_ASR_models" .


grep: ./__pycache__/models.cpython-311.pyc: binary file matches
./Demo/Inference_LibriTTS.ipynb:    "text_aligner = load_ASR_models(ASR_path, ASR_config)\n",
./Demo/Inference_LJSpeech.ipynb:    "text_aligner = load_ASR_models(ASR_path, ASR_config)\n",
./train_second.py:    text_aligner = load_ASR_models(ASR_path, ASR_config)
./train_first.py:        text_aligner = load_ASR_models(ASR_path, ASR_config)
./Colab/StyleTTS2_Demo_LibriTTS.ipynb:        "text_aligner = load_ASR_models(ASR_path, ASR_config)\n",
./Colab/StyleTTS2_Demo_LJSpeech.ipynb:        "text_aligner = load_ASR_models(ASR_path, ASR_config)\n",
./Colab/StyleTTS2_Finetune_Demo.ipynb:        "text_aligner = load_ASR_models(ASR_path, ASR_config)\n",
./models.py:def load_ASR_models(ASR_MODEL_PATH, ASR_MODEL_CONFIG):
./train_finetune_accelerate.py:    text_aligner = load_ASR_models(ASR_path, ASR_config)
./train_finetune.py:    text_aligner = load_ASR_models(ASR_path, ASR_config)


In [ ]:
!sed -n '/def load_ASR_models/,/^def/p' models.py



def load_ASR_models(ASR_MODEL_PATH, ASR_MODEL_CONFIG):
    # load ASR model
    def _load_config(path):
        with open(path) as f:
            config = yaml.safe_load(f)
        model_config = config['model_params']
        return model_config

    def _load_model(model_config, model_path):
        model = ASRCNN(**model_config)
        import torch.serialization
        torch.serialization.add_safe_globals([getattr])
        params = torch.load(model_path, map_location='cpu', weights_only=False)['model']
        model.load_state_dict(params)
        return model

    asr_model_config = _load_config(ASR_MODEL_CONFIG)
    asr_model = _load_model(asr_model_config, ASR_MODEL_PATH)
    _ = asr_model.train()

    return asr_model

def build_model(args, text_aligner, pitch_extractor, bert):


In [ ]:
# Read the original content
with open('models.py', 'r') as f:
    lines = f.readlines()

# Modify the lines containing the _load_model function
new_lines = []
inside_load_model = False
added_safe_globals = False

for i, line in enumerate(lines):
    if 'def _load_model' in line:
        inside_load_model = True

    if inside_load_model and 'torch.load(' in line:
        # Insert the add_safe_globals line *before* torch.load
        new_lines.append("        import torch.serialization\n")
        new_lines.append("        torch.serialization.add_safe_globals([getattr])\n")

        # Modify torch.load line to include weights_only=False
        line = line.replace('torch.load(model_path, map_location=\'cpu\')',
                            'torch.load(model_path, map_location=\'cpu\', weights_only=False)')

        inside_load_model = False  # done modifying

    new_lines.append(line)

# Write the modified content back to models.py
with open('models.py', 'w') as f:
    f.writelines(new_lines)



FileNotFoundError: [Errno 2] No such file or directory: 'models.py'

### Synthesize speech

#### Basic synthesis (5 diffusion steps, seen speakers)

In [ ]:
text = "'' StyleTTS 2 is a text to speech model that leverages style diffusion and adversarial training with large speech language models to achieve human level text to speech synthesis. ''" # @param {"type":"string"}


In [ ]:
reference_dicts = {}
reference_dicts['696_92939'] = "Demo/reference_audio/696_92939_000016_000006.wav"
reference_dicts['1789_142896'] = "Demo/reference_audio/1789_142896_000022_000005.wav"

In [ ]:
import nltk
nltk.download('punkt')


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

In [ ]:
noise = torch.randn(1,1,256).to(device)
for k, path in reference_dicts.items():
    ref_s = compute_style(path)
    start = time.time()
    wav = inference(text, ref_s, alpha=0.3, beta=0.7, diffusion_steps=5, embedding_scale=1)
    rtf = (time.time() - start) / (len(wav) / 24000)
    print(f"RTF = {rtf:5f}")
    import IPython.display as ipd
    print(k + ' Synthesized:')
    display(ipd.Audio(wav, rate=24000, normalize=False))
    print('Reference:')
    display(ipd.Audio(path, rate=24000, normalize=False))

RTF = 4.138006
696_92939 Synthesized:


Reference:


RTF = 4.269760
1789_142896 Synthesized:


Reference:


#### With higher diffusion steps (more diverse)

Since the sampler is ancestral, the higher the stpes, the more diverse the samples are, with the cost of slower synthesis speed.

In [ ]:
noise = torch.randn(1,1,256).to(device)
for k, path in reference_dicts.items():
    ref_s = compute_style(path)
    start = time.time()
    wav = inference(text, ref_s, alpha=0.3, beta=0.7, diffusion_steps=10, embedding_scale=1)
    rtf = (time.time() - start) / (len(wav) / 24000)
    print(f"RTF = {rtf:5f}")
    import IPython.display as ipd
    print(k + ' Synthesized:')
    display(ipd.Audio(wav, rate=24000, normalize=False))
    print(k + ' Reference:')
    display(ipd.Audio(path, rate=24000, normalize=False))

RTF = 3.442597
696_92939 Synthesized:


696_92939 Reference:


RTF = 2.905876
1789_142896 Synthesized:


1789_142896 Reference:


#### Basic synthesis (5 diffusion steps, unseen speakers)
The following samples are to reproduce samples in [Section 4](https://styletts2.github.io/#libri) of the demo page. All spsakers are unseen during training. You can compare the generated samples to popular zero-shot TTS models like Vall-E and NaturalSpeech 2.

In [ ]:
reference_dicts = {}
# format: (path, text)
reference_dicts['1221-135767'] = ("Demo/reference_audio/1221-135767-0014.wav", "Yea, his honourable worship is within, but he hath a godly minister or two with him, and likewise a leech.")
reference_dicts['5639-40744'] = ("Demo/reference_audio/5639-40744-0020.wav", "Thus did this humane and right minded father comfort his unhappy daughter, and her mother embracing her again, did all she could to soothe her feelings.")
reference_dicts['908-157963'] = ("Demo/reference_audio/908-157963-0027.wav", "And lay me down in my cold bed and leave my shining lot.")
reference_dicts['4077-13754'] = ("Demo/reference_audio/4077-13754-0000.wav", "The army found the people in poverty and left them in comparative wealth.")

In [ ]:
noise = torch.randn(1,1,256).to(device)
for k, v in reference_dicts.items():
    path, text = v
    ref_s = compute_style(path)
    start = time.time()
    wav = inference(text, ref_s, alpha=0.3, beta=0.7, diffusion_steps=5, embedding_scale=1)
    rtf = (time.time() - start) / (len(wav) / 24000)
    print(f"RTF = {rtf:5f}")
    import IPython.display as ipd
    print(k + ' Synthesized: ' + text)
    display(ipd.Audio(wav, rate=24000, normalize=False))
    print(k + ' Reference:')
    display(ipd.Audio(path, rate=24000, normalize=False))

RTF = 2.960367
1221-135767 Synthesized: Yea, his honourable worship is within, but he hath a godly minister or two with him, and likewise a leech.


1221-135767 Reference:


RTF = 4.436632
5639-40744 Synthesized: Thus did this humane and right minded father comfort his unhappy daughter, and her mother embracing her again, did all she could to soothe her feelings.


5639-40744 Reference:


RTF = 5.176268
908-157963 Synthesized: And lay me down in my cold bed and leave my shining lot.


908-157963 Reference:


RTF = 4.390674
4077-13754 Synthesized: The army found the people in poverty and left them in comparative wealth.


4077-13754 Reference:


### Speech expressiveness

The following section recreates the samples shown in [Section 6](https://styletts2.github.io/#emo) of the demo page. The speaker reference used is `1221-135767-0014.wav`, which is unseen during training.

#### With `embedding_scale=1`
This is the classifier-free guidance scale. The higher the scale, the more conditional the style is to the input text and hence more emotional.

In [ ]:
ref_s = compute_style("Demo/reference_audio/1221-135767-0014.wav")

In [ ]:
texts = {}
texts['Happy'] = "We are happy to invite you to join us on a journey to the past, where we will visit the most amazing monuments ever built by human hands."
texts['Sad'] = "I am sorry to say that we have suffered a severe setback in our efforts to restore prosperity and confidence."
texts['Angry'] = "The field of astronomy is a joke! Its theories are based on flawed observations and biased interpretations!"
texts['Surprised'] = "I can't believe it! You mean to tell me that you have discovered a new species of bacteria in this pond?"

for k,v in texts.items():
    wav = inference(v, ref_s, diffusion_steps=10, alpha=0.3, beta=0.7, embedding_scale=1)
    print(k + ": ")
    display(ipd.Audio(wav, rate=24000, normalize=False))

Happy: 


Sad: 


Angry: 


Surprised: 


#### With `embedding_scale=2`

In [ ]:
texts = {}
texts['Happy'] = "We are happy to invite you to join us on a journey to the past, where we will visit the most amazing monuments ever built by human hands."
texts['Sad'] = "I am sorry to say that we have suffered a severe setback in our efforts to restore prosperity and confidence."
texts['Angry'] = "The field of astronomy is a joke! Its theories are based on flawed observations and biased interpretations!"
texts['Surprised'] = "I can't believe it! You mean to tell me that you have discovered a new species of bacteria in this pond?"

for k,v in texts.items():
    noise = torch.randn(1,1,256).to(device)
    wav = inference(v, ref_s, diffusion_steps=10, alpha=0.3, beta=0.7, embedding_scale=2)
    print(k + ": ")
    display(ipd.Audio(wav, rate=24000, normalize=False))

#### With `embedding_scale=2, alpha = 0.5, beta = 0.9`
`alpha` and `beta` is the factor to determine much we use the style sampled based on the text instead of the reference. The higher the value of `alpha` and `beta`, the more suitable the style it is to the text but less similar to the reference. Using higher beta makes the synthesized speech more emotional, at the cost of lower similarity to the reference. `alpha` determines the timbre of the speaker while `beta` determines the prosody.

In [ ]:
texts = {}
texts['Happy'] = "We are happy to invite you to join us on a journey to the past, where we will visit the most amazing monuments ever built by human hands."
texts['Sad'] = "I am sorry to say that we have suffered a severe setback in our efforts to restore prosperity and confidence."
texts['Angry'] = "The field of astronomy is a joke! Its theories are based on flawed observations and biased interpretations!"
texts['Surprised'] = "I can't believe it! You mean to tell me that you have discovered a new species of bacteria in this pond?"

for k,v in texts.items():
    noise = torch.randn(1,1,256).to(device)
    wav = inference(v, ref_s, diffusion_steps=10, alpha=0.5, beta=0.9, embedding_scale=2)
    print(k + ": ")
    display(ipd.Audio(wav, rate=24000, normalize=False))

### Zero-shot speaker adaptation
This section recreates the "Acoustic Environment Maintenance" and "Speaker’s Emotion Maintenance" demo in [Section 4](https://styletts2.github.io/#libri) of the demo page. You can compare the generated samples to popular zero-shot TTS models like Vall-E. Note that the model was trained only on LibriTTS, which is about 250 times fewer data compared to those used to trian Vall-E with similar or better effect for these maintainance.

#### Acoustic Environment Maintenance

Since we want to maintain the acoustic environment in the speaker (timbre), we set  `alpha = 0` to make the speaker as close to the reference as possible while only changing the prosody according to the text.  

In [ ]:
reference_dicts = {}
# format: (path, text)
reference_dicts['3'] = ("Demo/reference_audio/3.wav", "As friends thing I definitely I've got more male friends.")
reference_dicts['4'] = ("Demo/reference_audio/4.wav", "Everything is run by computer but you got to know how to think before you can do a computer.")
reference_dicts['5'] = ("Demo/reference_audio/5.wav", "Then out in LA you guys got a whole another ball game within California to worry about.")

In [ ]:
noise = torch.randn(1,1,256).to(device)
for k, v in reference_dicts.items():
    path, text = v
    ref_s = compute_style(path)
    start = time.time()
    wav = inference(text, ref_s, alpha=0.0, beta=0.5, diffusion_steps=5, embedding_scale=1)
    rtf = (time.time() - start) / (len(wav) / 24000)
    print(f"RTF = {rtf:5f}")
    import IPython.display as ipd
    print('Synthesized: ' + text)
    display(ipd.Audio(wav, rate=24000, normalize=False))
    print('Reference:')
    display(ipd.Audio(path, rate=24000, normalize=False))

#### Speaker’s Emotion Maintenance

Since we want to maintain the emotion in the speaker (prosody), we set  `beta = 0.1` to make the speaker as closer to the reference as possible while having some diversity thruogh the slight timbre change.

In [ ]:
reference_dicts = {}
# format: (path, text)
reference_dicts['Anger'] = ("Demo/reference_audio/anger.wav", "We have to reduce the number of plastic bags.")
reference_dicts['Sleepy'] = ("Demo/reference_audio/sleepy.wav", "We have to reduce the number of plastic bags.")
reference_dicts['Amused'] = ("Demo/reference_audio/amused.wav", "We have to reduce the number of plastic bags.")
reference_dicts['Disgusted'] = ("Demo/reference_audio/disgusted.wav", "We have to reduce the number of plastic bags.")

In [ ]:
noise = torch.randn(1,1,256).to(device)
for k, v in reference_dicts.items():
    path, text = v
    ref_s = compute_style(path)
    start = time.time()
    wav = inference(text, ref_s, alpha=0.3, beta=0.1, diffusion_steps=10, embedding_scale=1)
    rtf = (time.time() - start) / (len(wav) / 24000)
    print(f"RTF = {rtf:5f}")
    import IPython.display as ipd
    print(k + ' Synthesized: ' + text)
    display(ipd.Audio(wav, rate=24000, normalize=False))
    print(k + ' Reference:')
    display(ipd.Audio(path, rate=24000, normalize=False))

### Longform Narration

This section includes basic implementation of Algorithm 1 in the paper for consistent longform audio generation. The example passage is taken from [Section 5](https://styletts2.github.io/#long) of the demo page.

In [ ]:
passage = passage = '''If the supply of fruit is greater than the family needs, it may be made a source of income by sending the fresh fruit to the market if there is one near enough, or by preserving, canning, and making jelly for sale. To make such an enterprise a success the fruit and work must be first class. There is magic in the word "Homemade," when the product appeals to the eye and the palate; but many careless and incompetent people have found to their sorrow that this word has not magic enough to float inferior goods on the market. As a rule large canning and preserving establishments are clean and have the best appliances, and they employ chemists and skilled labor. The home product must be very good to compete with the attractive goods that are sent out from such establishments. Yet for first class home made products there is a market in all large cities. All first-class grocers have customers who purchase such goods.''' # @param {type:"string"}

In [ ]:
# seen speaker
path = "Demo/reference_audio/696_92939_000016_000006.wav"
s_ref = compute_style(path)
sentences = passage.split('.') # simple split by comma
wavs = []
s_prev = None
for text in sentences:
    if text.strip() == "": continue
    text += '.' # add it back

    wav, s_prev = LFinference(text,
                              s_prev,
                              s_ref,
                              alpha = 0.3,
                              beta = 0.9,  # make it more suitable for the text
                              t = 0.7,
                              diffusion_steps=10, embedding_scale=1.5)
    wavs.append(wav)
print('Synthesized: ')
display(ipd.Audio(np.concatenate(wavs), rate=24000, normalize=False))
print('Reference: ')
display(ipd.Audio(path, rate=24000, normalize=False))

### Style Transfer

The following section demostrates the style transfer capacity for unseen speakers in [Section 6](https://styletts2.github.io/#emo) of the demo page. For this, we set `alpha=0.5, beta = 0.9` for the most pronounced effects (mostly using the sampled style).

In [ ]:
# reference texts to sample styles

ref_texts = {}
ref_texts['Happy'] = "We are happy to invite you to join us on a journey to the past, where we will visit the most amazing monuments ever built by human hands."
ref_texts['Sad'] = "I am sorry to say that we have suffered a severe setback in our efforts to restore prosperity and confidence."
ref_texts['Angry'] = "The field of astronomy is a joke! Its theories are based on flawed observations and biased interpretations!"
ref_texts['Surprised'] = "I can't believe it! You mean to tell me that you have discovered a new species of bacteria in this pond?"

In [ ]:
path = "Demo/reference_audio/1221-135767-0014.wav"
s_ref = compute_style(path)

text = "Yea, his honourable worship is within, but he hath a godly minister or two with him, and likewise a leech."
for k,v in ref_texts.items():
    wav = STinference(text, s_ref, v, diffusion_steps=10, alpha=0.5, beta=0.9, embedding_scale=1.5)
    print(k + ": ")
    display(ipd.Audio(wav, rate=24000, normalize=False))

ImportError: Numba needs NumPy 2.0 or less. Got NumPy 2.3.

### Speech diversity

This section reproduces samples in [Section 7](https://styletts2.github.io/#var) of the demo page.

`alpha` and `beta` determine the diversity of the synthesized speech. There are two extreme cases:
- If `alpha = 1` and `beta = 1`, the synthesized speech sounds the most dissimilar to the reference speaker, but it is also the most diverse (each time you synthesize a speech it will be totally different).
- If `alpha = 0` and `beta = 0`, the synthesized speech sounds the most siimlar to the reference speaker, but it is deterministic (i.e., the sampled style is not used for speech synthesis).


#### Default setting (`alpha = 0.3, beta=0.7`)
This setting uses 70% of the reference timbre and 30% of the reference prosody and use the diffusion model to sample them based on the text.

In [ ]:
# unseen speaker
path = "Demo/reference_audio/1221-135767-0014.wav"
ref_s = compute_style(path)

text = "How much variation is there?"
for _ in range(5):
    wav = inference(text, ref_s, diffusion_steps=10, alpha=0.3, beta=0.7, embedding_scale=1)
    display(ipd.Audio(wav, rate=24000, normalize=False))

#### Less diverse setting (`alpha = 0.1, beta=0.3`)
This setting uses 90% of the reference timbre and 70% of the reference prosody. This makes it more similar to the reference speaker at cost of less diverse samples.

In [ ]:
# unseen speaker
path = "Demo/reference_audio/1221-135767-0014.wav"
ref_s = compute_style(path)

text = "How much variation is there?"
for _ in range(5):
    wav = inference(text, ref_s, diffusion_steps=10, alpha=0.1, beta=0.3, embedding_scale=1)
    display(ipd.Audio(wav, rate=24000, normalize=False))

#### More diverse setting (`alpha = 0.5, beta=0.95`)
This setting uses 50% of the reference timbre and 5% of the reference prosody (so it uses 100% of the sampled prosody, which makes it more diverse), but this makes it more dissimilar to the reference speaker.  

In [ ]:
# unseen speaker
path = "Demo/reference_audio/1221-135767-0014.wav"
ref_s = compute_style(path)

text = "How much variation is there?"
for _ in range(5):
    wav = inference(text, ref_s, diffusion_steps=10, alpha=0.5, beta=0.95, embedding_scale=1)
    display(ipd.Audio(wav, rate=24000, normalize=False))

#### Extreme setting (`alpha = 1, beta=1`)
This setting uses 0% of the reference timbre and prosody and use the diffusion model to sample the entire style. This makes the speaker very dissimilar to the reference speaker.

In [ ]:
# unseen speaker
path = "Demo/reference_audio/1221-135767-0014.wav"
ref_s = compute_style(path)

text = "How much variation is there?"
for _ in range(5):
    wav = inference(text, ref_s, diffusion_steps=10, alpha=1, beta=1, embedding_scale=1)
    display(ipd.Audio(wav, rate=24000, normalize=False))

#### No variation (`alpha = 0, beta=0`)
This setting uses 100% of the reference timbre and prosody and do not use the diffusion model at all. This makes the speaker very similar to the reference speaker, but there is no variation.

In [ ]:
# unseen speaker
path = "Demo/reference_audio/1221-135767-0014.wav"
ref_s = compute_style(path)

text = "How much variation is there?"
for _ in range(5):
    wav = inference(text, ref_s, diffusion_steps=10, alpha=0, beta=0, embedding_scale=1)
    display(ipd.Audio(wav, rate=24000, normalize=False))

### Extra fun!

You can record your own voice and clone it using pre-trained StyleTTS 2 model here.

#### Run the following cell to record your voice for 5 seconds. Please keep speaking to have the best effect.

In [ ]:
# all imports
from IPython.display import Javascript
from google.colab import output
from base64 import b64decode

RECORD = """
const sleep  = time => new Promise(resolve => setTimeout(resolve, time))
const b2text = blob => new Promise(resolve => {
  const reader = new FileReader()
  reader.onloadend = e => resolve(e.srcElement.result)
  reader.readAsDataURL(blob)
})
var record = time => new Promise(async resolve => {
  stream = await navigator.mediaDevices.getUserMedia({ audio: true })
  recorder = new MediaRecorder(stream)
  chunks = []
  recorder.ondataavailable = e => chunks.push(e.data)
  recorder.start()
  await sleep(time)
  recorder.onstop = async ()=>{
    blob = new Blob(chunks)
    text = await b2text(blob)
    resolve(text)
  }
  recorder.stop()
})
"""

def record(sec=3):
  display(Javascript(RECORD))
  s = output.eval_js('record(%d)' % (sec*1000))
  b = b64decode(s.split(',')[1])
  with open('audio.wav','wb') as f:
    f.write(b)
  return 'audio.wav'  # or webm ?

#### Please run this cell and speak:

In [ ]:
print('Speak now for 5 seconds.')
audio = record(sec=5)
import IPython.display as ipd
display(ipd.Audio(audio, rate=24000, normalize=False))

#### Synthesize in your own voice

In [ ]:
text = ''' StyleTTS 2 is a text to speech model that leverages style diffusion and adversarial training with large speech language models to achieve human level text to speech synthesis. ''' # @param {type:"string"}


In [ ]:
reference_dicts = {}
reference_dicts['You'] = audio

In [ ]:
start = time.time()
noise = torch.randn(1,1,256).to(device)
for k, path in reference_dicts.items():
    ref_s = compute_style(path)

    wav = inference(text, ref_s, alpha=0.1, beta=0.5, diffusion_steps=5, embedding_scale=1)
    rtf = (time.time() - start) / (len(wav) / 24000)
    print('Speaker: ' + k)
    import IPython.display as ipd
    print('Synthesized:')
    display(ipd.Audio(wav, rate=24000, normalize=False))
    print('Reference:')
    display(ipd.Audio(path, rate=24000, normalize=False))

# **train**

**load wav files from LJspeech**

In [4]:
import yaml

config_path = "/content/StyleTTS2/Configs/config_ft.yml"

# Load the YAML config
with open(config_path, "r") as f:
    config = yaml.safe_load(f)

# Ensure the required section exists
if "data_params" not in config:
    config["data_params"] = {}

# Update the values
config["data_params"]["root_path"] = "/content/LJSpeech-1.1/wavs"
config["batch_size"] = 2  # 🔁 Change batch size here as needed
config["max_len"] = 100
# Save it back
with open(config_path, "w") as f:
    yaml.safe_dump(config, f)

print("✅ Updated root_path and batch_size in config_ft.yml")



✅ Updated root_path and batch_size in config_ft.yml


In [5]:
!wget https://data.keithito.com/data/speech/LJSpeech-1.1.tar.bz2
!tar -xvjf LJSpeech-1.1.tar.bz2


--2025-08-05 15:15:46--  https://data.keithito.com/data/speech/LJSpeech-1.1.tar.bz2
Resolving data.keithito.com (data.keithito.com)... 138.199.46.66, 2400:52e0:1500::945:1
Connecting to data.keithito.com (data.keithito.com)|138.199.46.66|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 2748572632 (2.6G) [text/plain]
Saving to: ‘LJSpeech-1.1.tar.bz2’

LJSpeech-1.1.tar.bz 100%[===================>]   2.56G  83.4MB/s    in 15s     

2025-08-05 15:16:01 (169 MB/s) - ‘LJSpeech-1.1.tar.bz2’ saved [2748572632/2748572632]

LJSpeech-1.1/
LJSpeech-1.1/metadata.csv
LJSpeech-1.1/wavs/
LJSpeech-1.1/wavs/LJ007-0048.wav
LJSpeech-1.1/wavs/LJ041-0060.wav
LJSpeech-1.1/wavs/LJ005-0133.wav
LJSpeech-1.1/wavs/LJ039-0220.wav
LJSpeech-1.1/wavs/LJ048-0274.wav
LJSpeech-1.1/wavs/LJ036-0043.wav
LJSpeech-1.1/wavs/LJ037-0129.wav
LJSpeech-1.1/wavs/LJ011-0265.wav
LJSpeech-1.1/wavs/LJ028-0418.wav
LJSpeech-1.1/wavs/LJ042-0116.wav
LJSpeech-1.1/wavs/LJ005-0143.wav
LJSpeech-1.1/wavs/LJ035-0083.wav

In [6]:
import os
import soundfile as sf

def filter_text_file(txt_path, wav_dir, max_samples=10):
    print(f"\n📄 Processing: {os.path.basename(txt_path)}")

    with open(txt_path, "r", encoding="utf-8") as f:
        lines = f.readlines()

    valid_lines = []
    deleted_corrupt_files = []

    for line in lines:
        if len(valid_lines) >= max_samples:
            break

        parts = line.strip().split("|")
        if not parts:
            continue

        wav_file = parts[0]
        full_path = os.path.join(wav_dir, wav_file)

        if os.path.exists(full_path):
            try:
                data, sr = sf.read(full_path, always_2d=True)
                if data.size == 0 or sr <= 0:
                    raise ValueError("Empty or invalid audio data")
                valid_lines.append(line)
            except Exception as e:
                print(f"❌ Corrupt: {wav_file} → {e}")
                try:
                    os.remove(full_path)
                    deleted_corrupt_files.append(wav_file)
                    print(f"🗑️ Deleted corrupt file: {wav_file}")
                except Exception as delete_err:
                    print(f"⚠️ Failed to delete: {wav_file} → {delete_err}")

    # Overwrite the text file with only valid entries
    with open(txt_path, "w", encoding="utf-8") as f:
        f.writelines(valid_lines)

    print(f"✅ Valid entries written: {len(valid_lines)}")
    print(f"🗑️ Corrupt files deleted: {len(deleted_corrupt_files)}")


# === Paths ===
base_dir = "/content/StyleTTS2/Data"
wav_dir = "/content/LJSpeech-1.1/wavs"

# === Process all three splits ===
filter_text_file(os.path.join(base_dir, "train_list.txt"), wav_dir)
filter_text_file(os.path.join(base_dir, "val_list.txt"), wav_dir)




📄 Processing: train_list.txt
✅ Valid entries written: 10
🗑️ Corrupt files deleted: 0

📄 Processing: val_list.txt
✅ Valid entries written: 7
🗑️ Corrupt files deleted: 0


In [7]:
import os
import random
import soundfile as sf

# Paths
ood_txt_path = "/content/StyleTTS2/Data/OOD_texts.txt"
ljspeech_wav_dir = "/content/LJSpeech-1.1/wavs"

# Step 1: Get all wav files from LJSpeech
all_ljspeech_wavs = [f for f in os.listdir(ljspeech_wav_dir) if f.endswith(".wav")]
random.shuffle(all_ljspeech_wavs)

# Step 2: Filter 10 valid (non-corrupt) wav files
valid_wavs = []
for wav_file in all_ljspeech_wavs:
    wav_path = os.path.join(ljspeech_wav_dir, wav_file)
    try:
        data, sr = sf.read(wav_path)
        if data.size == 0 or sr <= 0:
            raise ValueError("Empty or invalid audio")
        valid_wavs.append(wav_file)
        if len(valid_wavs) == 10:
            break
    except Exception as e:
        print(f"❌ Skipped corrupt: {wav_file} → {e}")

if len(valid_wavs) < 10:
    raise ValueError("❌ Could not find 10 valid LJSpeech wav files.")

# Step 3: Read original OOD lines
with open(ood_txt_path, "r", encoding="utf-8", errors="replace") as f:
    ood_lines = [line.strip() for line in f if "|" in line]

# Step 4: Modify only the first 10 lines, replace filename, discard rest
new_ood_lines = []
for i in range(10):
    parts = ood_lines[i].split("|")
    parts[0] = valid_wavs[i]  # Replace only the wav filename
    new_line = "|".join(parts)
    new_ood_lines.append(new_line)

# Step 5: Overwrite OOD_texts.txt with exactly 10 modified lines
with open(ood_txt_path, "w", encoding="utf-8") as f:
    f.write("\n".join(new_ood_lines) + "\n")

print("✅ OOD_texts.txt updated with exactly 10 valid dummy LJSpeech samples.")


✅ OOD_texts.txt updated with exactly 10 valid dummy LJSpeech samples.


**val.txt nd OOD.txt**

In [8]:
%cd StyleTTS2

/content/StyleTTS2


In [9]:
import librosa

In [ ]:
!ls /content/phoneme_to_viseme.json


/content/phoneme_to_viseme.json


In [ ]:
!ls /content/LJSpeech-1.1/wavs/LJ033-0149.wav



/content/LJSpeech-1.1/wavs/LJ033-0149.wav


In [18]:
from pydub import AudioSegment
from IPython.display import Audio
from google.colab import files

# Define the path
wav_path = "/content/LJSpeech-1.1/wavs/LJ033-0173.wav"
mp3_path = "/content/bbb_audio.mp3"

# Convert WAV to MP3
sound = AudioSegment.from_wav(wav_path)
sound.export(mp3_path, format="mp3")

# Optional: Play in notebook
display(Audio(mp3_path))

# Download the MP3
files.download(mp3_path)


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [19]:
!pip install git+https://github.com/openai/whisper.git
!sudo apt install ffmpeg

import whisper

# Load model
model = whisper.load_model("base")  # use "small", "medium", or "large" for better accuracy

# Upload your audio
from google.colab import files
uploaded = files.upload()  # Upload your 'sample1_audio (8).mp3'

# Transcribe
audio_path = list(uploaded.keys())[0]
result = model.transcribe(audio_path)
print("Grapheme-based transcription:\n")
print(result["text"])


  Cloning https://github.com/openai/whisper.git to /tmp/pip-req-build-gs2agwb0
  Running command git clone --filter=blob:none --quiet https://github.com/openai/whisper.git /tmp/pip-req-build-gs2agwb0
  Resolved https://github.com/openai/whisper.git to commit c0d2f624c09dc18e709e37c2ad90c039a4eb72a2
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
ffmpeg is already the newest version (7:4.4.2-0ubuntu0.22.04.1).
0 upgraded, 0 newly installed, 0 to remove and 35 not upgraded.


Saving bbb_audio.mp3 to bbb_audio.mp3
Grapheme-based transcription:

 The papers I also found were similar in fiber composition, therefore in addition to the visual characteristics.


In [ ]:
!python train_finetune.py


python3: can't open file '/content/train_finetune.py': [Errno 2] No such file or directory


In [20]:
!python train_finetune_inf.py --inference --audio_path=LJ033-0173.wav --text="The papers I also found were similar in fiber composition, therefore in addition to the visual characteristics."

2025-08-05 15:23:32.787812: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1754407412.821584    4042 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1754407412.832490    4042 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-08-05 15:23:32.864472: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
bert loaded
bert_encoder loaded
predictor loaded
decoder loaded
text_encoder loaded
predictor_encoder loaded
style_en

In [13]:
import json

phoneme_to_viseme = {
    " ": 0,
    "$": 0,
    "i": 6,
    "ɪ": 6,
    "eɪ": 4,
    "ɛ": 4,
    "æ": 1,
    "ɑ": 2,
    "ɔ": 3,
    "ʊ": 4,
    "oʊ": 8,
    "u": 7,
    "ʌ": 1,
    "aɪ": 11,
    "aʊ": 9,
    "ɔɪ": 10,
    "ju": 6,
    "ə": 1,
    "ɪɹ": 6,
    "ɛɹ": 4,
    "ʊɹ": 4,
    "aɪɹ": 11,
    "aʊɹ": 9,
    "ɔɹ": 3,
    "ɑɹ": 2,
    "ɝ": 5,
    "ɚ": 1,
    "p": 21,
    "b": 21,
    "t": 19,
    "d": 19,
    "k": 20,
    "g": 20,
    "m": 21,
    "n": 19,
    "ŋ": 20,
    "f": 18,
    "v": 18,
    "θ": 19,
    "ð": 17,
    "s": 15,
    "z": 15,
    "ʃ": 16,
    "ʒ": 16,
    "h": 12,
    "tʃ": 19,
    "dʒ": 19,
    "l": 14,
    "ɹ": 13,
    "w": 7,
    "j": 6,
    "aː": 2,
    "a": 2,
    "ɛː": 4,
    "iː": 6,
    "øː": 1,
    "oː": 8,
    "œ": 4,
    "e": 4,
    "eː": 4,
    "uː": 7,
    "yː": 4,
    "ʏ": 7,
    "ai": 2,
    "au": 2,
    "ɔy": 3,
    "ɔʏ̯": 3,
    "ʤ": 16,
    "pf": 21,
    "ʀ": 13,
    "ʁ": 13,
    "ts": 19,
    "ç": 12,
    "ɐ": 4,
    "ʔ": 19,
    "ɨ": 6,
    "pʲ": 21,
    "bʲ": 21,
    "tʲ": 19,
    "dʲ": 19,
    "kʲ": 20,
    "gʲ": 20,
    "x": 12,
    "xʲ": 12,
    "fʲ": 18,
    "vʲ": 18,
    "sʲ": 15,
    "zʲ": 15,
    "ʂ": 15,
    "ʐ": 15,
    "t͡s": 19,
    "t͡ɕ": 19,
    "ɕː": 16,
    "mʲ": 21,
    "nʲ": 19,
    "lʲ": 14,
    "r": 13,
    "rʲ": 13,
    "ɑ̃": 2,
    "ø": 1,
    "ɛ̃": 4,
    "ɔ̃": 3,
    "o": 8,
    "œ̃": 4,
    "y": 4,
    "ɲ": 19,
    "ɥ": 7,
    "n‿": 19,
    "t‿": 19,
    "z‿": 15,
    "β": 21,
    "t͡ʃ": 19,
    "ɣ": 20,
    "j͡j": 6,
    "ʎ": 14,
    "ɾ": 19
}

with open("/content/phoneme_to_viseme.json", "w", encoding="utf-8") as f:
    json.dump(phoneme_to_viseme, f, ensure_ascii=False, indent=4)

print("phoneme_to_viseme.json saved successfully!")


phoneme_to_viseme.json saved successfully!


In [ ]:
import torch
torch.cuda.empty_cache()


In [ ]:
import os
import json



file_path = "/content/StyleTTS2/train_finetune.py"  # update if needed

# Define the debug block (without indentation)
debug_block_raw = [
    "# ----------------- DEBUG PATCH START -----------------",
    "import json",
    "with open('/content/phoneme_to_viseme.json', 'r', encoding='utf-8') as f:",
    "    phoneme_to_viseme = json.load(f)",
    "if i == 0:",
    "    sa = s2s_attn.detach().cpu()",
    "    mo = s2s_attn_mono.detach().cpu()",
    "    te = t_en.detach().cpu()",
    "    ar = asr.detach().cpu()",
    "    dg = d_gt.detach().cpu()",
    "    ph_ids = texts[0].cpu().tolist()",
    "    durations = dg[0].tolist()",
    "",
    "    print(f\"\\n[DEBUG] Epoch {epoch}, Batch {i}\")",
    "    print(\"  s2s_attn.shape:\", sa.shape)",
    "    print(\"  s2s_attn sample [0, :3, :3]:\\n\", sa[0, :3, :3].numpy())",
    "    print(\"  s2s_attn_mono.shape:\", mo.shape)",
    "    print(\"  s2s_attn_mono sample [0, :3, :3]:\\n\", mo[0, :3, :3].numpy())",
    "    print(\"  t_en.shape:\", te.shape)",
    "    print(\"  t_en sample [0, :3, :3]:\\n\", te[0, :3, :3].numpy())",
    "    print(\"  asr.shape:\", ar.shape)",
    "    print(\"  asr sample [0, :3, :3]:\\n\", ar[0, :3, :3].numpy())",
    "    print(\"  d_gt.shape:\", dg.shape)",
    "    print(\"  d_gt sample [0, :10]:\", durations[:10])",
    "",
    "    print(\"\\n[Phoneme ↔ Duration and Start Time (ms) for sample 0]:\")",
    "",
    "    try:",
    "        import json",
    "        id2ph = {v: k for k, v in train_dataloader.dataset.text_cleaner.word_index_dictionary.items()}",
    "        skip_symbols = set(';:,.!?¡¿—…\\\"«»“”ǃˈˌːˑʼ˞↓↑→↗↘̩ᵻ')",
    "        frame_duration_ms = 25.0",
    "        start_ms = 0.0",
    "        output_json = []",
    "",
    "        # Build full list of (symbol, duration) pairs",
    "        full_phonemes = [(id2ph.get(pid, f\"[UNK_{pid}]\"), dur) for pid, dur in zip(ph_ids, durations)]",
    "",
    "        # Trim padding at start and end ('$')",
    "        #while full_phonemes and full_phonemes[0][0] == '$':",
    "            #full_phonemes.pop(0)",
    "        #while full_phonemes and full_phonemes[-1][0] == '$':",
    "            #full_phonemes.pop()",
    "",
    "        for symbol, dur in full_phonemes:",
    "            duration_ms = dur * frame_duration_ms",
    "            if symbol in skip_symbols:",
    "                start_ms += duration_ms",
    "                continue",
    "            print(f\"    {symbol} → {int(dur)} frames, start at {int(start_ms)} ms, duration {int(duration_ms)} ms\")",
    "            duration_ms = dur * frame_duration_ms",
    "",
    "            viseme_id = phoneme_to_viseme.get(symbol)",
    "            if viseme_id is None:",
    "                continue",
    "",
    "            output_json.append({",
    "                \"offset\": round(start_ms, 3),",
    "                \"visemeId\": viseme_id",
    "            })",
    "",
    "            start_ms += duration_ms",
    "",
    "        print(\"\\n[Viseme JSON Output]:\")",
    "        print(json.dumps(output_json, indent=4))",
    "",
    "    except Exception as e:",
    "        print(\"    [Couldn't print phoneme mappings — check dataset.text_cleaner or phoneme_to_viseme]\")",
    "        print(\"    Error:\", e)",
    "# ----------------- DEBUG PATCH END -----------------",
]

In [ ]:
import os
import json



file_path = "/content/StyleTTS2/train_finetune.py"  # update if needed

# ----------------- DEBUG PATCH START -----------------
if i == 0:
    import json
    with open('/content/phoneme_to_viseme.json', 'r', encoding='utf-8') as f:
        phoneme_to_viseme = json.load(f)

    sa = s2s_attn.detach().cpu()
    mo = s2s_attn_mono.detach().cpu()
    te = t_en.detach().cpu()
    ar = asr.detach().cpu()
    dg = d_gt.detach().cpu()
    ph_ids = texts[0].cpu().tolist()
    durations = dg[0].tolist()

    # Check if batch_paths is available and get filename
    sample_wav = batch_paths[0].split("/")[-1] if ('batch_paths' in locals() and batch_paths) else "UNKNOWN.wav"

    # ONLY process if this is the target file
    target_wav = "LJ028-0184.wav"
    if sample_wav == target_wav:
        print(f"\n[DEBUG] Epoch {epoch}, Batch {i}")
        print("  s2s_attn.shape:", sa.shape)
        print("  s2s_attn_mono.shape:", mo.shape)
        print("  t_en.shape:", te.shape)
        print("  asr.shape:", ar.shape)
        print("  d_gt sample [0, :10]:", durations[:10])
        print(f"\n[Sample WAV File]: {sample_wav}")
        print("\n[Phoneme ↔ Duration and Start Time (ms) for sample 0]:")

        try:
            id2ph = {v: k for k, v in train_dataloader.dataset.text_cleaner.word_index_dictionary.items()}
            skip_symbols = set(';:,.!?¡¿—…\\"«»“”ǃˈˌːˑʼ˞↓↑→↗↘̩ᵻ')
            frame_duration_ms = 25.0
            output_json = []
            viseme_output = []

            full_phonemes = [(id2ph.get(pid, f"[UNK_{pid}]"), dur) for pid, dur in zip(ph_ids, durations)]

            start_ms = 0.0
            for symbol, dur in full_phonemes:
                duration_ms = dur * frame_duration_ms
                if symbol in skip_symbols:
                    print(f"  [SKIPPED] {symbol} ({int(dur)} frames)")
                else:
                    print(f"    {symbol} → {int(dur)} frames, start at {int(start_ms)} ms, duration {int(duration_ms)} ms")
                    viseme_id = phoneme_to_viseme.get(symbol)
                    if viseme_id is not None:
                        output_json.append({
                            "symbol": symbol,
                            "start_ms": int(start_ms),
                            "duration_ms": int(duration_ms),
                            "viseme_id": viseme_id
                        })
                        viseme_output.append({
                            "offset": round(start_ms, 3),
                            "visemeId": viseme_id
                        })
                start_ms += duration_ms

            print(f"\n[Viseme JSON Output for: {sample_wav}]")
            print(json.dumps(viseme_output, indent=4))

            import sys
            sys.exit(0)  # ⛔ STOP training immediately

        except Exception as e:
            print("    [Couldn't print phoneme mappings — check dataset.text_cleaner or phoneme_to_viseme]")
            print("    Error:", e)
# ----------------- DEBUG PATCH END -----------------














# Read original file
with open(file_path, "r", encoding="utf-8") as f:
    lines = f.readlines()

# Remove previous debug patch
start_marker = "# ----------------- DEBUG PATCH START -----------------"
end_marker = "# ----------------- DEBUG PATCH END -----------------"
inside_patch = False
cleaned_lines = []
for line in lines:
    if start_marker in line:
        inside_patch = True
        continue
    if end_marker in line:
        inside_patch = False
        continue
    if not inside_patch:
        cleaned_lines.append(line)

# Find insert location
insert_index = -1
for idx, line in enumerate(cleaned_lines):
    if "d_gt = s2s_attn_mono.sum" in line:
        insert_index = idx + 1
        base_indent = line[:len(line) - len(line.lstrip())]
        break

# Apply indentation to debug block
debug_block = [base_indent + line + "\n" if line.strip() else "\n" for line in debug_block_raw]

# Insert into cleaned_lines
if insert_index != -1:
    cleaned_lines = cleaned_lines[:insert_index] + debug_block + cleaned_lines[insert_index:]
else:
    raise RuntimeError("⚠️ Couldn't find insertion point for debug patch (d_gt line missing).")

# Write back to file
with open(file_path, "w", encoding="utf-8") as f:
    f.writelines(cleaned_lines)

print("✅ Debug patch inserted successfully into:", file_path)


✅ Debug patch inserted successfully into: /content/StyleTTS2/train_finetune.py


**patches**

In [14]:
file_path = "/content/StyleTTS2/train_finetune.py"

# Define the patch code for torch.load
patch_code = [
    "\n# -------- PATCH torch.load during model loading --------\n",
    "old_torch_load = torch.load\n",
    "def torch_load_weights_only_false(*args, **kwargs):\n",
    "    kwargs['weights_only'] = False\n",
    "    return old_torch_load(*args, **kwargs)\n",
    "torch.load = torch_load_weights_only_false\n\n"
]

# Read original file
with open(file_path, "r") as f:
    lines = f.readlines()

# Insert the CUDA memory setting line at the very top
lines.insert(0, 'import os\nos.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"\n')

# Remove any existing copy of the patch
filtered_lines = []
skip_mode = False
for line in lines:
    if "PATCH torch.load" in line:
        skip_mode = True
    if not skip_mode:
        filtered_lines.append(line)
    if skip_mode and line.strip() == "":
        skip_mode = False  # stop skipping after blank line following patch

# Insert patch right after "import torch"
new_lines = []
inserted = False
for line in filtered_lines:
    new_lines.append(line)
    if not inserted and line.strip() == "import torch":
        new_lines.extend(patch_code)
        inserted = True

# Write back the modified file
with open(file_path, "w") as f:
    f.writelines(new_lines)

print("✅ Patch inserted and CUDA memory config set in train_finetune.py")



✅ Patch inserted and CUDA memory config set in train_finetune.py


In [15]:
file_path = "/content/StyleTTS2/models.py"

# The patch line to replace in torch.load(...)
patch_old = "params = torch.load(model_path, map_location='cpu')['model']"
patch_new = "params = torch.load(model_path, map_location='cpu', weights_only=False)['model']"

# Read original file
with open(file_path, "r") as f:
    lines = f.readlines()

new_lines = []
for line in lines:
    if patch_old in line:
        # Replace the line with patch_new
        new_lines.append(line.replace(patch_old, patch_new))
    else:
        new_lines.append(line)

# Write back the modified file
with open(file_path, "w") as f:
    f.writelines(new_lines)

print("✅ Modified torch.load in models.py to add weights_only=False")


✅ Modified torch.load in models.py to add weights_only=False


In [16]:
file_path = "/content/StyleTTS2/meldataset.py"  # adjust if needed

# Read file
with open(file_path, "r", encoding="utf-8") as f:
    lines = f.readlines()

# Clean any old patch lines
lines = [line for line in lines if "idx2ph = {i: s for s, i in dicts.items()}" not in line]
lines = [line for line in lines if "self.idx2ph = idx2ph" not in line]
lines = [line for line in lines if "self.pad_id" not in line]

# Step 1: Insert idx2ph = ... after dicts = {}
idx_line = -1
for i, line in enumerate(lines):
    if "dicts = {}" in line:
        idx_line = i
        break
if idx_line == -1:
    raise RuntimeError("❌ Could not find 'dicts = {}'")

lines.insert(idx_line + 1, "idx2ph = {i: s for s, i in dicts.items()}  # ID → phoneme mapping\n")

# Step 2: Insert self.idx2ph after self.text_cleaner = TextCleaner()
patched = False
for i, line in enumerate(lines):
    if "self.text_cleaner = TextCleaner()" in line:
        indent = len(line) - len(line.lstrip())
        lines.insert(i + 1, " " * indent + "self.idx2ph = idx2ph  # phoneme ID → symbol mapping\n")
        patched = True
        break

if not patched:
    raise RuntimeError("❌ Could not find 'self.text_cleaner = TextCleaner()' to patch dataset class")

# Save back to file
with open(file_path, "w", encoding="utf-8") as f:
    f.writelines(lines)

print("✅ Successfully re-patched `meldataset.py` — cleaned old lines and re-inserted `idx2ph` properly.")


✅ Successfully re-patched `meldataset.py` — cleaned old lines and re-inserted `idx2ph` properly.


In [ ]:
import torch
print(torch.__version__)

2.6.0+cu124


In [ ]:
!pip show transformers

Name: transformers
Version: 4.52.4
Summary: State-of-the-art Machine Learning for JAX, PyTorch and TensorFlow
Home-page: https://github.com/huggingface/transformers
Author: The Hugging Face team (past and future) with the help of all our contributors (https://github.com/huggingface/transformers/graphs/contributors)
Author-email: transformers@huggingface.co
License: Apache 2.0 License
Location: /usr/local/lib/python3.11/dist-packages
Requires: filelock, huggingface-hub, numpy, packaging, pyyaml, regex, requests, safetensors, tokenizers, tqdm
Required-by: peft, sentence-transformers


In [ ]:


!pip install transformers==4.48.1

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.4/44.4 kB 2.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.7/9.7 MB 71.2 MB/s eta 0:00:00
  Attempting uninstall: transformers
    Found existing installation: transformers 4.52.4
    Uninstalling transformers-4.52.4:
      Successfully uninstalled transformers-4.52.4


In [ ]:
!pip uninstall -y torch torchaudio




Found existing installation: torch 2.6.0
Uninstalling torch-2.6.0:
  Successfully uninstalled torch-2.6.0
Found existing installation: torchaudio 2.5.0+cu121
Uninstalling torchaudio-2.5.0+cu121:
  Successfully uninstalled torchaudio-2.5.0+cu121


In [ ]:
!pip install torch==2.5.1 torchaudio==2.5.1 --index-url https://download.pytorch.org/whl/cu121



Looking in indexes: https://download.pytorch.org/whl/cu121
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 780.5/780.5 MB 2.5 MB/s eta 0:00:00
  Using cached https://download.pytorch.org/whl/cu121/torchaudio-2.5.1%2Bcu121-cp311-cp311-linux_x86_64.whl (3.4 MB)
  Using cached https://download.pytorch.org/whl/cu121/nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached https://download.pytorch.org/whl/cu121/nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached https://download.pytorch.org/whl/cu121/nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached https://download.pytorch.org/whl/cu121/nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl (410.6 MB)
  Using cached https://download.pytorch.org/whl/cu121/nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl (121.6 MB)
  Using cached https://download.pytorch.org/whl/cu121/nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.wh

In [ ]:
Runtime > Restart runtime


SyntaxError: invalid syntax (ipython-input-13-2796588790.py, line 1)

**extract phoneme duration.py**

In [ ]:
_pad = "$"
_punctuation = ';:,.!?¡¿—…"«»“” '
_letters = 'ABCDEFGHIJKLMNOPQRSTUVWXYZabcdefghijklmnopqrstuvwxyz'
_letters_ipa = "ɑɐɒæɓʙβɔɕçɗɖðʤəɘɚɛɜɝɞɟʄɡɠɢʛɦɧħɥʜɨɪʝɭɬɫɮʟɱɯɰŋɳɲɴøɵɸθœɶʘɹɺɾɻʀʁɽʂʃʈʧʉʊʋⱱʌɣɤʍχʎʏʑʐʒʔʡʕʢǀǁǂǃˈˌːˑʼʴʰʱʲʷˠˤ˞↓↑→↗↘'̩'ᵻ"

# Export all symbols:
symbols = [_pad] + list(_punctuation) + list(_letters) + list(_letters_ipa)

dicts = {}
for i in range(len((symbols))):
    dicts[symbols[i]] = i

class TextCleaner:
    def __init__(self, dummy=None):
        self.word_index_dictionary = dicts
    def __call__(self, text):
        indexes = []
        for char in text:
            try:
                indexes.append(self.word_index_dictionary[char])
            except KeyError:
                print(text)
        return indexes

In [ ]:
text_cleaner = TextCleaner()

In [ ]:
text = text_cleaner(' aɪv bˌɪn tə θɹˈiː ʌv ðoʊz ɪntˈɛlɪdʒəns ˈɑːfɪsᵻzðˌoʊ wˌaɪ ðeɪ kˈɔːl ðˌɛm ðæt aɪ kˈænt ɪmˈædʒɪn.|813')


 aɪv bˌɪn tə θɹˈiː ʌv ðoʊz ɪntˈɛlɪdʒəns ˈɑːfɪsᵻzðˌoʊ wˌaɪ ðeɪ kˈɔːl ðˌɛm ðæt aɪ kˈænt ɪmˈædʒɪn.|813
 aɪv bˌɪn tə θɹˈiː ʌv ðoʊz ɪntˈɛlɪdʒəns ˈɑːfɪsᵻzðˌoʊ wˌaɪ ðeɪ kˈɔːl ðˌɛm ðæt aɪ kˈænt ɪmˈædʒɪn.|813
 aɪv bˌɪn tə θɹˈiː ʌv ðoʊz ɪntˈɛlɪdʒəns ˈɑːfɪsᵻzðˌoʊ wˌaɪ ðeɪ kˈɔːl ðˌɛm ðæt aɪ kˈænt ɪmˈædʒɪn.|813
 aɪv bˌɪn tə θɹˈiː ʌv ðoʊz ɪntˈɛlɪdʒəns ˈɑːfɪsᵻzðˌoʊ wˌaɪ ðeɪ kˈɔːl ðˌɛm ðæt aɪ kˈænt ɪmˈædʒɪn.|813
